<img src="images/intake-rooki-demo.png" width=500 alt="Intake Rooki Demo"></img>

---

# Using intake-esgf with rooki
Here we dig into using intake-esgf to search for data, then rooki to do server-side computing!

---

## Overview
If you have an introductory paragraph, lead with it here! Keep it short and tied to your material, then be sure to continue into the required list of topics below,

1. Search and find data using intake-esgf, returning the dataset ids
1. Feed the dataset ids to rooki to subset and average the data remotely
1. Visualize the results on the end-user side

## Prerequisites

| Concepts | Importance | Notes |
| --- | --- | --- |
| [Intro to Intake-ESGF](intro-search) | Necessary | How to configure a search and use output |
| [Intro to Rooki](rooki) | Helpful | How to initialize and run rooki |
| [Intro to hvPlot](https://hvplot.holoviz.org/user_guide/Geographic_Data.html) | Necessary | How to plot interactive visualizations |

- **Time to learn**: 30 minutes

---

## Imports

In [1]:
import os

# Set the rooki client to use the oak ridge national lab (ORNL) WPS deployment
url = 'https://esgf-wps.apps.onyx.ccs.ornl.gov/wps'
os.environ['ROOK_URL'] = url

from rooki import rooki
from rooki import operators as ops
import intake_esgf
from intake_esgf import ESGFCatalog
import xarray as xr
import hvplot.xarray
import holoviews as hv
import panel as pn
hv.extension("bokeh")

## Search and Find Data for Surface Temperature on DKRZ Node

Let's start with refining which index we would like to search from. For this analysis, we are remotely computing on the ORNL node since this is where rooki is running. We know this from checking the `._url` method of rooki!

In [2]:
rooki._url

'https://esgf-wps.apps.onyx.ccs.ornl.gov/wps'

### Set the Index Node and Search
We need to ensure only the Oak Ridge National Lab (ORNL) index node is active, not the Argonne National Laboratory (ANL) node. We can accomplish this using the configuration settings for intake-esgf.

In [4]:
intake_esgf.conf.set(indices={"anl-dev":False,
                              "ornl-dev":True,
                              }
                    )

cat = ESGFCatalog()

cat = ESGFCatalog()
cat.search(
        activity_id='CMIP',
        experiment_id=["historical",],
        variable_id=["tas"],
        member_id='r1i1p1f1',
        grid_label='gn',
        table_id="Amon",
        institution_id=["MIROC", "NCAR", "NASA-GISS", "CMCC"]
    )
cat.df

   Searching indices:   0%|          |0/1 [       ?index/s]

mip_era experiment_id variable_id        source_id   version grid_label  \
0    CMIP6    historical         tas      GISS-E2-2-H  20191120         gn   
1    CMIP6    historical         tas        CMCC-ESM2  20210114         gn   
2    CMIP6    historical         tas      CESM2-WACCM  20190227         gn   
3    CMIP6    historical         tas     CMCC-CM2-SR5  20200616         gn   
4    CMIP6    historical         tas      GISS-E2-1-G  20180827         gn   
5    CMIP6    historical         tas      GISS-E2-2-G  20191120         gn   
6    CMIP6    historical         tas  CESM2-WACCM-FV2  20191120         gn   
8    CMIP6    historical         tas        CESM2-FV2  20191120         gn   
9    CMIP6    historical         tas     CMCC-CM2-HR4  20200904         gn   
10   CMIP6    historical         tas      GISS-E2-1-H  20190403         gn   
15   CMIP6    historical         tas            CESM2  20190308         gn   
16   CMIP6    historical         tas   GISS-E2-1-G-CC  20190815         gn   
22   CMIP6    historical         tas           MIROC6  20181212         gn   

   member_id table_id institution_id activity_drs project  \
0   r1i1p1f1     Amon      NASA-GISS         CMIP   CMIP6   
1   r1i1p1f1     Amon           CMCC         CMIP   CMIP6   
2   r1i1p1f1     Amon           NCAR         CMIP   CMIP6   
3   r1i1p1f1     Amon           CMCC         CMIP   CMIP6   
4   r1i1p1f1     Amon      NASA-GISS         CMIP   CMIP6   
5   r1i1p1f1     Amon      NASA-GISS         CMIP   CMIP6   
6   r1i1p1f1     Amon           NCAR         CMIP   CMIP6   
8   r1i1p1f1     Amon           NCAR         CMIP   CMIP6   
9   r1i1p1f1     Amon           CMCC         CMIP   CMIP6   
10  r1i1p1f1     Amon      NASA-GISS         CMIP   CMIP6   
15  r1i1p1f1     Amon           NCAR         CMIP   CMIP6   
16  r1i1p1f1     Amon      NASA-GISS         CMIP   CMIP6   
22  r1i1p1f1     Amon          MIROC         CMIP   CMIP6   

                                                   id  
0   [CMIP6.CMIP.NASA-GISS.GISS-E2-2-H.historical.r...  
1   [CMIP6.CMIP.CMCC.CMCC-ESM2.historical.r1i1p1f1...  
2   [CMIP6.CMIP.NCAR.CESM2-WACCM.historical.r1i1p1...  
3   [CMIP6.CMIP.CMCC.CMCC-CM2-SR5.historical.r1i1p...  
4   [CMIP6.CMIP.NASA-GISS.GISS-E2-1-G.historical.r...  
5   [CMIP6.CMIP.NASA-GISS.GISS-E2-2-G.historical.r...  
6   [CMIP6.CMIP.NCAR.CESM2-WACCM-FV2.historical.r1...  
8   [CMIP6.CMIP.NCAR.CESM2-FV2.historical.r1i1p1f1...  
9   [CMIP6.CMIP.CMCC.CMCC-CM2-HR4.historical.r1i1p...  
10  [CMIP6.CMIP.NASA-GISS.GISS-E2-1-H.historical.r...  
15  [CMIP6.CMIP.NCAR.CESM2.historical.r1i1p1f1.Amo...  
16  [CMIP6.CMIP.NASA-GISS.GISS-E2-1-G-CC.historica...  
22  [CMIP6.CMIP.MIROC.MIROC6.historical.r1i1p1f1.A...

## Extract the Dataset ID and Pass to Rooki
Now that we have set of datasets, we need to extract the `dataset_id`, which is the unique identifier for the dataset. We can pull this from the `id` column from `intake-esgf`

### Separate the Dataset ID

In [5]:
cat.df.id.values[0]

['CMIP6.CMIP.NASA-GISS.GISS-E2-2-H.historical.r1i1p1f1.Amon.tas.gn.v20191120|esgf-data04.diasjp.net',
 'CMIP6.CMIP.NASA-GISS.GISS-E2-2-H.historical.r1i1p1f1.Amon.tas.gn.v20191120|dpesgf03.nccs.nasa.gov',
 'CMIP6.CMIP.NASA-GISS.GISS-E2-2-H.historical.r1i1p1f1.Amon.tas.gn.v20191120|esgf-node.ornl.gov']

Notice how the node information is added onto end of the file id. We need to "chop off" that last bit, leaving everything before the `|` character. We put this into a function to make it easier to generalize and apply.

In [6]:
def separate_dataset_id(full_dataset):
    """
    Create the path to the data, adding an additional css03_data to indicate the CMIP6 archive at ORNL
    """
    return f"css03_data.{full_dataset[0].split('|')[0]}"

separate_dataset_id(cat.df.id.values[0])

'css03_data.CMIP6.CMIP.NASA-GISS.GISS-E2-2-H.historical.r1i1p1f1.Amon.tas.gn.v20191120'

Now, we can apply this to the entire list within our dataframe using the following

In [7]:
dsets = [separate_dataset_id(dataset) for dataset in list(cat.df.id.values)]
dsets

['css03_data.CMIP6.CMIP.NASA-GISS.GISS-E2-2-H.historical.r1i1p1f1.Amon.tas.gn.v20191120',
 'css03_data.CMIP6.CMIP.CMCC.CMCC-ESM2.historical.r1i1p1f1.Amon.tas.gn.v20210114',
 'css03_data.CMIP6.CMIP.NCAR.CESM2-WACCM.historical.r1i1p1f1.Amon.tas.gn.v20190227',
 'css03_data.CMIP6.CMIP.CMCC.CMCC-CM2-SR5.historical.r1i1p1f1.Amon.tas.gn.v20200616',
 'css03_data.CMIP6.CMIP.NASA-GISS.GISS-E2-1-G.historical.r1i1p1f1.Amon.tas.gn.v20180827',
 'css03_data.CMIP6.CMIP.NASA-GISS.GISS-E2-2-G.historical.r1i1p1f1.Amon.tas.gn.v20191120',
 'css03_data.CMIP6.CMIP.NCAR.CESM2-WACCM-FV2.historical.r1i1p1f1.Amon.tas.gn.v20191120',
 'css03_data.CMIP6.CMIP.NCAR.CESM2-FV2.historical.r1i1p1f1.Amon.tas.gn.v20191120',
 'css03_data.CMIP6.CMIP.CMCC.CMCC-CM2-HR4.historical.r1i1p1f1.Amon.tas.gn.v20200904',
 'css03_data.CMIP6.CMIP.NASA-GISS.GISS-E2-1-H.historical.r1i1p1f1.Amon.tas.gn.v20190403',
 'css03_data.CMIP6.CMIP.NCAR.CESM2.historical.r1i1p1f1.Amon.tas.gn.v20190308',
 'css03_data.CMIP6.CMIP.NASA-GISS.GISS-E2-1-G-CC.

### Compute with Rooki
Now that we have a list of IDs to pass to rooki, let's compute!

In this case, we are:
- Subsetting from the year 1900 to 2000
- Subsetting near India using the bounds `65,0,100,35`
- Computing the yealy average

We then check to make sure the response is okay, and if it is, return that to the user!

In [8]:
def compute_annual_mean_subset(dset_id):
    # Subset by area then time
    wf = ops.AverageByTime(
        ops.Subset(
            ops.Input(
                'tas', [dsets[0]]
            ),
            time='1900-01-01/2000-12-31',
            area='65,0,100,35',
        ),
    freq="year"
    )
    
    resp = wf.orchestrate()
    
    if resp.ok:
        ds = resp.datasets()[0]
    else:
        ds = xr.Dataset()
    return ds

In [9]:
compute_annual_mean_subset(dsets[0])

Metalink content-type detected.


<xarray.Dataset> Size: 156kB
Dimensions:    (lat: 18, time: 101, bnds: 2, lon: 14)
Coordinates:
  * lat        (lat) float64 144B 1.0 3.0 5.0 7.0 9.0 ... 29.0 31.0 33.0 35.0
  * lon        (lon) float64 112B 66.25 68.75 71.25 73.75 ... 93.75 96.25 98.75
    height     float64 8B ...
  * time       (time) object 808B 1900-01-01 00:00:00 ... 2000-01-01 00:00:00
Dimensions without coordinates: bnds
Data variables:
    lat_bnds   (time, lat, bnds) float64 29kB ...
    lon_bnds   (time, lon, bnds) float64 23kB ...
    tas        (time, lat, lon) float32 102kB ...
    time_bnds  (time, bnds) object 2kB ...
Attributes: (12/48)
    Conventions:            CF-1.7 CMIP-6.2
    activity_id:            CMIP
    branch_method:          standard
    branch_time_in_child:   0.0
    branch_time_in_parent:  0.0
    contact:                Kenneth Lo (cdkkl@giss.nasa.gov)
    ...                     ...
    title:                  GISS-E2-2-H output prepared for CMIP6
    tracking_id:            hdl:21.14100/09d7bd73-f74e-4f9a-a14b-205fa5078217
    variable_id:            tas
    variant_label:          r1i1p1f1
    license:                CMIP6 model data produced by NASA Goddard Institu...
    cmor_version:           3.3.2

Now that it works with a single dataset, let's do this for all the datasets and put them into a dictionary with the dataset ids as the keys.

In [10]:
dset_dict = {}
for dset in dsets:
    dset_dict[dset] = compute_annual_mean_subset(dset)

Metalink content-type detected.
Metalink content-type detected.
Metalink content-type detected.
Metalink content-type detected.
Metalink content-type detected.
Metalink content-type detected.
Metalink content-type detected.
Metalink content-type detected.
Metalink content-type detected.
Metalink content-type detected.
Metalink content-type detected.
Metalink content-type detected.
Metalink content-type detected.


## Visualize the Output
Let's use hvPlot to visualize. The datasets are stored in a dictionary of datasets, we need to:
- Extract a single key
- Plot a contour filled visualization, with some geographic features

In [11]:
dset_dict[list(dset_dict.keys())[-1]].tas.hvplot.contourf(x='lon',
                                                          y='lat',
                                                          cmap='Reds',
                                                          levels=20,
                                                          clim=(250, 320),
                                                          features=["land", "ocean"],
                                                          alpha=0.7,
                                                          widget_location='bottom',
                                                          clabel="Yearly Average Temperature (K)",
                                                          geo=True)

Column
    [0] HoloViews(DynamicMap, sizing_mode='fixed', widget_location='bottom')
    [1] WidgetBox(align=('center', 'end'))
        [0] DiscreteSlider(name='time', options={'1900-01-01 00:00:00': cf...}, value=cftime.DatetimeNoLeap(1900...)

---

## Summary
Within this notebook, we learned how to specify a specific index node to search from, pass discovered datasets to rooki, and chain remote-compute with several operations using rooki. We then visualized the output using hvPlot, leading to an interactive plot!

### What's next?
More adaptations of the intake-esgf + rooki to remotely compute on ESGF data.

## Resources and references
 - [intake-esgf documentation](https://intake-esgf.readthedocs.io/en/latest/)
 - [rooki documentation](https://rooki.readthedocs.io/en/latest/)
 - [Working with geographic data with hvPlot](https://hvplot.holoviz.org/user_guide/Geographic_Data.html)
